In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pwd

/content


In [ ]:
currentdir =  "/content/drive/MyDrive/DataMining"


In [ ]:
!pip install ray

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torch.nn import BCEWithLogitsLoss
import pickle
from collections import defaultdict
from torch.optim import AdamW
import itertools
import ray
from sklearn.utils import resample

from ray import tune
from ray.tune import CLIReporter
from ray.tune.schedulers import ASHAScheduler
import csv
from sklearn.metrics import f1_score, accuracy_score
import os.path
from tqdm import tqdm
from functools import partial
import psutil
import numpy as np
import pandas
from ast import literal_eval

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
ray._private.utils.get_system_memory = lambda: psutil.virtual_memory().total

## ***Basic Neural Network Model***

In [ ]:
class Net(nn.Module):

    def __init__(self, input_size, num_layers, max_layer_size, drop_out):
        super(Net, self).__init__()
        self.input_size = input_size
        self.num_layers = num_layers
        self.max_layer_size = max_layer_size
        in_size = max_layer_size

        self.layers = nn.ModuleList([nn.Linear(input_size, in_size)])
        for layer in range(1, num_layers-1):
            self.layers.append(nn.Linear(in_size, int(in_size/2)))
            in_size = int(in_size/2)
        self.layers.append(nn.Linear(in_size, 1))
        self.drop_out = nn.Dropout(drop_out)


    def forward(self, x):
        for layer in self.layers[:-1]:
            x = F.relu(self.drop_out(layer(x)))
        x = self.layers[-1](x)
        x = torch.sigmoid(x)
        return x

## ***DataSet Loader***

In [ ]:
from torch.utils import data
class HatespeechDataset(Dataset):
    def __init__(self, filename, stemming=True, upsample=True):
    
        data = pandas.read_csv(filename, sep=";")

        if stemming:
            features = ["id", "label", "tfidf_stemmed_tokens", "tfidf_stemmed_hashtags"]
        else:
            features = ["id", "label", "tfidf_lemmatized_tokens", "tfidf_lemmatized_hashtags"]
        data = data[features]
        if upsample:
            data_minority = data[data.label == 1]
            data_majority = data[data.label == 0]
            data_minority = resample(data_minority, replace = True, n_samples=len(data_majority), random_state=55)
            data = pandas.concat([data_majority, data_minority])
        self.data=[]
        for dp in data.values:
            self.data.append([dp[0],dp[1], np.array(literal_eval(dp[2])), np.array(literal_eval(dp[3]))])
        
                
    def __len__(self):
        return len(self.data)
    
    def __getitem__(self, idx):
        ids = self.data[idx][0]
        tfidfs = self.data[idx][2:]
        label = self.data[idx][1]
        return ids, tfidfs, label


In [ ]:
a = HatespeechDataset(data_dir + "220505_train_data_preprocessed.csv", upsample=True)
a[2]

(19310,
 [array([-4.96687487e-02, -2.35883403e-02, -1.31236747e-02, -1.54114509e-02,
         -2.23165386e-02, -5.65288093e-03, -2.00280655e-02, -3.70941416e-02,
          5.16380485e-02,  7.85655748e-02,  1.53713009e-03, -1.60499690e-02,
         -1.96335022e-03,  1.70452335e-01,  1.47520850e-01, -3.99815114e-02,
          3.00066043e-02, -3.87255123e-03, -3.63250194e-02, -1.87400190e-03,
         -1.64011786e-02,  9.64651399e-04,  6.61092860e-02, -1.48738172e-02,
          1.24452927e-02, -1.29938921e-02, -2.09716416e-02, -2.44505338e-02,
         -3.97998988e-02, -1.00794863e-02, -2.60203749e-02, -1.75932950e-02,
         -4.60794274e-03, -2.11011734e-02,  2.11687114e-03,  7.60542017e-03,
         -1.67004484e-02, -1.74590702e-02,  6.05233054e-03,  1.01577181e-02,
         -6.54732954e-03, -9.84958630e-03, -1.00723576e-02, -1.31136541e-02,
          1.85849385e-02, -1.00817327e-02, -3.01661914e-03, -1.22146593e-02,
         -3.26121753e-03, -3.24737076e-04,  2.31015933e-03, -5.87817

## ***Hyperparameter Optimisation***

In [ ]:
!ls ./drive/MyDrive/DataMining/Data_mining/data

220502_test_data_preprocessed.csv   220505_validation_data_preprocessed.csv
220502_train_data_preprocessed.csv  test_tweets.csv
220505_test_data_preprocessed.csv   train_tweet.csv
220505_train_data_preprocessed.csv


In [197]:
checkpoint_dir = currentdir + "/checkpoints"
data_dir = currentdir + "/Data_mining/data/"

config = {
    "lr": tune.loguniform(1e-3, 1e-1),
    "batch_size": tune.choice([8, 16, 32, 64]),
    "num_layers": tune.choice([2, 3, 4]),
    "drop_out" : tune.loguniform(0.1, 0.8),
    "max_layer_size": tune.choice(list(range(200, 800, 100))),
}

scheduler = ASHAScheduler(
    metric="f1",
    mode="max",
    max_t=10000, #No time restrictions
    grace_period=4, 
    reduction_factor=2) 

reporter = CLIReporter(
    parameter_columns=["lr", "batch_size", "num_layers", "drop_out", "max_layer_size"],
    metric_columns=["f1", "training_iteration"])

result = tune.run(
        partial(train, checkpoint_dir=checkpoint_dir, data_dir = data_dir),
        resources_per_trial={"cpu": 1, "gpu": 1},
        config=config,
        num_samples=30, 
        scheduler=scheduler,
        progress_reporter=reporter)
    
best_trial = result.get_best_trial("f1", "max", "all")
print("Best trial config: {}".format(best_trial.config))
print("Best trial final validation: {}".format(
    best_trial.last_result["f1"]))

train_dataset = HatespeechDataset(data_dir + "220505_train_data_preprocessed.csv")
vector_size = train_dataset.data[0][2].shape[-1] + train_dataset.data[0][3].shape[-1] #Get size of representations
del train_dataset
best_trained_model = Net(vector_size, best_trial.config["num_layers"], best_trial.config["max_layer_size"], best_trial.config["drop_out"])
best_trained_model.to(device)

best_checkpoint_dir = best_trial.checkpoint.value
model_state, optimizer_state = torch.load(os.path.join(
    best_checkpoint_dir, "checkpoint"))
torch.save(model_state, './nn.model')
torch.save(best_trial.config, './nn.config')

best_trained_model.load_state_dict(model_state)
test(best_trained_model, best_trial.config, data_dir)


2022-05-09 14:57:18,396	WARNING callback.py:126 -- The TensorboardX logger cannot be instantiated because either TensorboardX or one of it's dependencies is not installed. Please make sure you have the latest version of TensorboardX installed: `pip install -U tensorboardx`
2022-05-09 14:57:18,613	INFO trial_runner.py:803 -- starting train_524e4_00000


== Status ==
Current time: 2022-05-09 14:57:18 (running for 00:00:00.26)
Memory usage on this node: 3.7/25.5 GiB
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 8192.000: None | Iter 4096.000: None | Iter 2048.000: None | Iter 1024.000: None | Iter 512.000: None | Iter 256.000: None | Iter 128.000: None | Iter 64.000: None | Iter 32.000: None | Iter 16.000: None | Iter 8.000: None | Iter 4.000: None
Resources requested: 1.0/4 CPUs, 1.0/1 GPUs, 0.0/15.0 GiB heap, 0.0/7.5 GiB objects (0.0/1.0 accelerator_type:T4)
Result logdir: /root/ray_results/train_2022-05-09_14-57-18
Number of trials: 16/30 (15 PENDING, 1 RUNNING)
+-------------------+----------+------------------+------------+--------------+--------------+------------+------------------+
| Trial name        | status   | loc              |         lr |   batch_size |   num_layers |   drop_out |   max_layer_size |
|-------------------+----------+------------------+------------+--------------+--------------+------------+-------------

(func pid=55750) tcmalloc: large alloc 1073741824 bytes == 0x48f1c000 @  0x7f8f373692a4 0x7f8d3a9269a5 0x7f8d3a927cc1 0x7f8d3a92969e 0x7f8d3a8fa50c 0x7f8d3a907399 0x7f8d3a8ef97a 0x59afff 0x515655 0x549e0e 0x593fce 0x511e2c 0x549576 0x593fce 0x511e2c 0x593dd7 0x5118f8 0x549576 0x4bca8a 0x5134a6 0x549e0e 0x593fce 0x548ae9 0x5127f1 0x549576 0x4bca8a 0x532b86 0x594a96 0x548cc1 0x5127f1 0x549576


== Status ==
Current time: 2022-05-09 14:57:30 (running for 00:00:12.56)
Memory usage on this node: 4.7/25.5 GiB
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 8192.000: None | Iter 4096.000: None | Iter 2048.000: None | Iter 1024.000: None | Iter 512.000: None | Iter 256.000: None | Iter 128.000: None | Iter 64.000: None | Iter 32.000: None | Iter 16.000: None | Iter 8.000: None | Iter 4.000: None
Resources requested: 1.0/4 CPUs, 1.0/1 GPUs, 0.0/15.0 GiB heap, 0.0/7.5 GiB objects (0.0/1.0 accelerator_type:T4)
Result logdir: /root/ray_results/train_2022-05-09_14-57-18
Number of trials: 17/30 (16 PENDING, 1 RUNNING)
+-------------------+----------+------------------+------------+--------------+--------------+------------+------------------+
| Trial name        | status   | loc              |         lr |   batch_size |   num_layers |   drop_out |   max_layer_size |
|-------------------+----------+------------------+------------+--------------+--------------+------------+-------------

  0%|          | 0/1301 [00:00<?, ?it/s]/usr/local/lib/python3.7/dist-packages/ray/workers/default_worker.py:19: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(func pid=55750)   parser.add_argument(
(func pid=55750) /usr/local/lib/python3.7/dist-packages/ray/workers/default_worker.py:20: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(func pid=55750)   "--node-ip-address",
(func pid=55750) /usr/local/lib/python3.7/dist-packages/ray/workers/default_worker.py:22: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(func pid=55750)   type=str,
100%|█████

...

(func pid=75967) [4,  2000] loss: 0.050
== Status ==
Current time: 2022-05-09 16:26:43 (running for 01:29:25.32)
Memory usage on this node: 4.7/25.5 GiB
Using AsyncHyperBand: num_stopped=24
Bracket: Iter 8192.000: None | Iter 4096.000: None | Iter 2048.000: None | Iter 1024.000: None | Iter 512.000: None | Iter 256.000: None | Iter 128.000: None | Iter 64.000: None | Iter 32.000: None | Iter 16.000: 0.8200891125575098 | Iter 8.000: 0.7836978874555992 | Iter 4.000: 0.7750730282375853
Resources requested: 1.0/4 CPUs, 1.0/1 GPUs, 0.0/15.0 GiB heap, 0.0/7.5 GiB objects (0.0/1.0 accelerator_type:T4)
Result logdir: /root/ray_results/train_2022-05-09_14-57-18
Number of trials: 30/30 (1 RUNNING, 29 TERMINATED)
+-------------------+------------+------------------+------------+--------------+--------------+------------+------------------+----------+----------------------+
| Trial name        | status     | loc              |         lr |   batch_size |   num_layers |   drop_out |   max_layer_siz

100%|██████████| 2602/2602 [00:06<00:00, 417.91it/s]
(func pid=75967) /usr/local/lib/python3.7/dist-packages/ray/workers/default_worker.py:46: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(func pid=75967)   help="the password to use for Redis",
(func pid=75967) /usr/local/lib/python3.7/dist-packages/ray/workers/default_worker.py:47: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(func pid=75967)   )
(func pid=75967) /usr/local/lib/python3.7/dist-packages/ray/workers/default_worker.py:49: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
(func pid=7

Result for train_524e4_00029:
  date: 2022-05-09_16-26-45
  done: true
  experiment_id: 7854c2fd2fa944ddb3aa8b8c9424ea50
  f1: 0.7413651315789473
  hostname: 7cc1ac6f52f7
  iterations_since_restore: 4
  node_ip: 172.28.0.2
  pid: 75967
  should_checkpoint: true
  time_since_restore: 137.99968433380127
  time_this_iter_s: 6.59535813331604
  time_total_s: 137.99968433380127
  timestamp: 1652113605
  timesteps_since_restore: 0
  training_iteration: 4
  trial_id: 524e4_00029
  warmup_time: 0.003306150436401367
  
== Status ==
Current time: 2022-05-09 16:26:45 (running for 01:29:26.92)
Memory usage on this node: 4.7/25.5 GiB
Using AsyncHyperBand: num_stopped=25
Bracket: Iter 8192.000: None | Iter 4096.000: None | Iter 2048.000: None | Iter 1024.000: None | Iter 512.000: None | Iter 256.000: None | Iter 128.000: None | Iter 64.000: None | Iter 32.000: None | Iter 16.000: 0.8200891125575098 | Iter 8.000: 0.7836978874555992 | Iter 4.000: 0.7700058453415866
Resources requested: 0/4 CPUs, 0/1 GP

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:13: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  del sys.path[0]
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:14: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:16: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  app.launch_new_instance()


TEST SET F1 SCORE: 0.8081731183722735
TEST SET ACCURACY: 0.8125210650488709


## ***Train***

In [ ]:
def train(config, checkpoint_dir, data_dir):
    train_dataset = HatespeechDataset(data_dir + "220505_train_data_preprocessed.csv", upsample=True)
    dev_dataset = HatespeechDataset(data_dir + "220505_validation_data_preprocessed.csv")
    train_dataloader = DataLoader(train_dataset, batch_size=config["batch_size"], shuffle=True)
    dev_dataloader = DataLoader(dev_dataset, batch_size=config["batch_size"])

    vector_size = train_dataset.data[0][2].shape[-1] + train_dataset.data[0][3].shape[-1] #Get size of representations
    net = Net(vector_size, config["num_layers"], config["max_layer_size"], config["drop_out"]).to(device)

    criterion = nn.BCELoss() 
    optimizer = AdamW(net.parameters(), lr=config["lr"])

    for epoch in range(20):  # loop over the dataset multiple times

        net.train()
        running_loss = 0.0
        for i, data in enumerate(tqdm(train_dataloader)):
            ids, tfidfs, labels = data
            tfidf_words = torch.tensor(tfidfs[0]).to(device)
            tfidf_hash = torch.tensor(tfidfs[1]).to(device)
            tfidfs = torch.concat((tfidf_words, tfidf_hash), dim=1)
            labels = torch.tensor(labels).to(device)

            # zero the parameter gradients
            optimizer.zero_grad()

            outputs = net(tfidfs.float())

            loss = criterion(outputs.squeeze(), labels.float())
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            if i % 2000 == 1999:
                print(f'[{epoch + 1}, {i + 1:5d}] loss: {running_loss / 2000:.3f}')
                running_loss = 0.0
        
        net.eval()
        preds = []
        label_list = []
        with torch.no_grad():

            for i, data in enumerate(dev_dataloader):
                ids, tfidfs, labels = data
                tfidf_words = torch.tensor(tfidfs[0]).to(device)
                tfidf_hash = torch.tensor(tfidfs[1]).to(device)
                tfidfs = torch.concat((tfidf_words, tfidf_hash), dim=1)
                labels = torch.tensor(labels).to(device)

                outputs = net(tfidfs.float())
                outputs = outputs.squeeze()

                preds.extend([bool(round(output))
                 for output in outputs.tolist()])
                label_list.extend([label for label in labels.tolist()])
            
            f1 = f1_score(label_list, preds)

            with tune.checkpoint_dir(epoch) as checkpoint_dir:
                path = os.path.join(checkpoint_dir, "checkpoint")
                torch.save((net.state_dict(), optimizer.state_dict()), path)
                        
            tune.report(f1=f1)


## ***Test***

In [ ]:
def test(net, config, data_dir):

    test_dataset = HatespeechDataset(data_dir + "220505_test_data_preprocessed.csv")
    test_dataloader = DataLoader(test_dataset, batch_size=config["batch_size"])

    net.eval()
    preds = []
    label_list = []
    with torch.no_grad():

        for i, data in enumerate(test_dataloader):
            ids, tfidfs, labels = data
            tfidf_words = torch.tensor(tfidfs[0]).to(device)
            tfidf_hash = torch.tensor(tfidfs[1]).to(device)
            tfidfs = torch.concat((tfidf_words, tfidf_hash), dim=1)
            labels = torch.tensor(labels).to(device)

            outputs = net(tfidfs.float())
            outputs = outputs.squeeze()
            preds.extend([bool(round(output)) for output in outputs.tolist()])
            label_list.extend([label for label in labels.tolist()])

        
        f1 = f1_score(label_list, preds)
        print("TEST SET F1 SCORE:", f1)
        acc = accuracy_score(label_list, preds)
        print("TEST SET ACCURACY:", acc)
